In [3]:
#====================================================================================
#    Proof-of-concept SageMath 9.2 implementation of the exponentiation algorithms
#    proposed in 
#    " Rebuttal to claims in Section 2.1 of the ePrint report 2021/583 
#    'Entropoid-based cryptography is group exponentiation in disguise' "
#
#    Copyright 2020, 2021:
#    Danilo Gligoroski, <danilog@ntnu.no>
#    Department of Information Security and Communication Technology,
#    Faculty of Information Technology and Electrical Engineering,
#    Norwegian University of Science and Technology - NTNU,
#    O.S.Bragstads plass 2B, 
#    N-7034 Trondheim, Norway
#
#    This program is free software: you can redistribute it and/or modify
#    it under the terms of the GNU General Public License as published by
#    the Free Software Foundation, either version 3 of the License, or
#    (at your option) any later version.
#
#    This program is distributed in the hope that it will be useful,
#    but WITHOUT ANY WARRANTY; without even the implied warranty of
#    MERCHANTABILITY or FITNESS FOR A PARTICULAR PURPOSE.  See the
#    GNU General Public License for more details.
#
#    You should have received a copy of the GNU General Public License
#    along with this program.  If not, see <https://www.gnu.org/licenses/>.
#====================================================================================

In [24]:
import numpy as np
import matplotlib.pyplot as plt

from matplotlib.colors import LogNorm
from numpy import ma
from matplotlib import ticker, cm
from sage.plot.contour_plot import ContourPlot

import re
import scipy
import scipy.stats

import random

flatten = lambda l: [item for sublist in l for item in sublist] 

# Finds a prime p = 2 q + 1 such that q is the the smallest prime 
# larger than 2^(lambda_bits - 2) + 2^(lambda_bits - 3)
def get_fixed_safe_prime(nbits = 128):
    # nbits should be >= 3
    global p, q
    q = next_prime(2^(nbits-2) + 2^(nbits - 3))
    search = True
    while search:
        p = 2*q + 1
        search = not(is_prime(p))
        q = next_prime(q)
    return p

def get_random_safe_prime(nbits = 128):
    # nbits should be >= 3
    global p, q
    q = random_prime(2^(nbits-2), false, 2^(nbits - 3))
    search = True
    while search:
        p = 2*q + 1
        search = not(is_prime(p))
        q = next_prime(q)
    return p

def get_random_entropoid_coefficients():
    global aa1, aa3, aa4, aa8, bb1, bb2, bb5, bb7, E_Zero, E_left_unit
    global F, p
    aa3 = F.random_element()
    aa8 = 0
    while aa8 == 0:
        aa8 = F.random_element(); 
    bb2 = F.random_element()
    bb7 = 0
    while bb7 == 0:
        bb7 = F.random_element(); 

    aa1 = (aa3*(aa8*bb2 - bb7))/(aa8*bb7)
    aa4 = (aa8*bb2)/bb7
    bb1 = -((bb2*(aa8 - aa3*bb7))/(aa8*bb7))
    bb5 = (aa3*bb7)/aa8

    E_Zero = vector((-(aa3/aa8), -(bb2/bb7)))
    E_left_unit = vector((-(aa3/aa8) + 1/bb7, 1/aa8 - bb2/bb7))
    
    pass

def mmult( X, Y ):
    global aa1, aa3, aa4, aa8, bb1, bb2, bb5, bb7
    f1 = aa8*X[1]*Y[0] + aa3*X[1] + aa4*Y[0] + aa1;
    f2 = bb7*X[0]*Y[1] + bb2*X[0] + bb5*Y[1] + bb1;
    return(vector((f1, f2)))

def pplus(x, y):
    global E_Zero
    return(vector(x)+vector(y)-vector(E_Zero))

def mminus(x, y):
    global E_Zero
    return(vector(x)-vector(y)+vector(E_Zero))

def iinverse(x):
    global aa3, bb2, bb7, aa8
    return(vector(((1 - aa3 * bb2 - aa3 * bb7 * x[1])/(aa8 * (bb2 + bb7 * x[1])), \
           (1 - aa3 * bb2 - aa8 * bb2 * x[0])/(bb7 * (aa3 + aa8 * x[0])))))

# D-transform transforms bijectively an m-dimensional list of entropoid elements
def D_transform(x):
    global m
    z = [0 for i in range(m)]
    z[0] = x[0]
    for i in range(1, m):
        z[i] = mmult(x[i-1], x[i])
    return(z)

# Multiplication of two m-dimensional entropoid elements with an entropic operation mmult
# is again an m-dimensional entropic operation. 
# Credit to the idea of Nager and Jianfang, ePrint report 2021/444
def multi_dim_mult(X, Y):
    global m, middle_derangement, Rounds, Leaders
    f1 = [mmult(X[i], Y[i]) for i in range(m)]
    for j in range(Rounds):
        f1 = D_transform(f1)
        f1[0] = mmult(Leaders[j], f1[0])
        f1 = middle_derangement.action(f1)
    f2 = [mmult(Y[i], f1[i]) for i in range(m)]
    return(f2)

def get_random_entropoid_nonzero_element():
    A0 = E_Zero[0]
    while A0 == E_Zero[0]:
        A0 = F.random_element(); 
    A1 = E_Zero[1]
    while A1 == E_Zero[1]:
        A1 = F.random_element(); 
    A = (A0, A1)
    return(vector(A))

def get_random_entropoid_element():
    A0 = F.random_element(); 
    A1 = F.random_element(); 
    A = (A0, A1)
    return(vector(A))

def Narayana_sequence(base):
    seq = [binomial(base - 1, i) * binomial(base - 1, i - 1)/(base - 1) for i in range(1, base)]
    return(seq)

def Catalan_number(b):
    return((binomial(2*b, b))/(b+1))

def get_base_max(p):
    maxvalue = (p-1)^2
    bmax = 1
    while Catalan_number(bmax) < maxvalue:
        bmax += 1
    return(bmax)

def get_all_bracketing(n, base):
    nndigits = n.digits(base-1)
    nrdigits = len(nndigits)
    maxvalue = ZZ([base - 2 for i in range(nrdigits-1)], base-1)
    PPall = [ZZ(i).digits(base-1, padto=nrdigits-1) for i in range(maxvalue+1)]
    return(PPall)

# A procedure that given an integer n, and a base b
# produces an array of integers with values between 0 and b - 2 (including b - 2)
# The length of the array is the same as the length of n interpreted in the base base
def get_random_bracketing(n, base):
    bracket_pattern = [ random.randint(0, base - 2) for i in range(len(n.digits(base))) ]
    return(bracket_pattern)


# A procedure that produces a random power index
# The range of a is between 1 and (p - 1)^m
# Once a is obtained, the bracketing is obtained by calling a procedure 
# for random bracketing a in the used base.
def get_random_power_index(base):
    global p, m
    a = ZZ(random.randint(1, (p-1)^m))
    a_pattern = get_random_bracketing(a, base)
    return([a, a_pattern, base])


# If we want to generate the bracketing sapes we can use this procedure
def allassocrules(n):
    rules = ['mmult(gg,gg)']
    for i in range(n-2):
        qq = rules[0]
        tmp = 'mmult(' + qq + ',gg)'
        for j in range(len(rules)):
            rules[j] = 'mmult(gg,' + rules[j] + ')'
        rules.append(tmp)
    return (rules)

# Let us generate all basic bracketing shapes as defined in
# Definition 17 of the paper "Entropoid Based Cryptography"
limitbases = 258
AssocRulesForDifferentBases = [[] for i in range(limitbases)]
for i in range(2, limitbases):
    AssocRulesForDifferentBases[i] = allassocrules(i)

# This is a computational procedure that gives the same result as 
# we would have evaluated the symbolic bracketing AssocRulesForDifferentBases[base][digit]
def AssocRuleForBaseAndDigit(gg, base, digit):
    j = 0
    tmp = mmult(gg, gg)
    if digit == 0:
        while j < base - 2:
            tmp = mmult(gg, tmp)
            j += 1
        return(tmp)
    else:
        while j < digit - 1:
            tmp = mmult(gg, tmp)
            j += 1
        if j <= base - 2:
            tmp = mmult(tmp, gg)
            j += 1
        while j < base - 2:
            tmp = mmult(gg, tmp)
            j += 1
        return(tmp)


# For the original one-dimensional Entropoids
# This is the central and most important procedure for
# non-abelian and non-associative exponentiation of g 
# to the power index nn = [n, n_pattern, base] 
def nanapow(g, nn):
    n = nn[0]
    pattern = nn[1]
    base = nn[2]

    digitss = n.digits(base)

    # Compute equations (39) from the paper
    gg = g
    powlist = [gg]
    for i in range(1, len(pattern)):
        gg = AssocRuleForBaseAndDigit(gg, base, pattern[i])
        powlist.append(gg)

    # find the index of the first non-zero element
    ii = digitss.index(next(filter(lambda x: x!=0, digitss))) 
    
    # Compute equations (40) from the paper
    if digitss[ii] == 1:
        result = powlist[ii]
    else:
        gg = powlist[ii]
        result = AssocRuleForBaseAndDigit(gg, digitss[ii], pattern[ii]%(digitss[ii] - 1))

    # Compute equations (41) from the paper
    ii += 1
    while ii<len(digitss):
        if digitss[ii] != 0:
            if digitss[ii] == 1:
                tmp = powlist[ii]
            else:
                gg = powlist[ii]
                tmp = AssocRuleForBaseAndDigit(gg, digitss[ii], pattern[ii]%(digitss[ii] - 1))
            if pattern[ii-1]%2 == 0:
                result = mmult(tmp, result)                
            else:
                result = mmult(result, tmp)
        ii += 1
    
    return(result)

# A procedure that finds a generator of the multiplicative quasigroup (\mathbb{E}_{(p-1)^2}^*, *)
def find_generator_p():
    global F, p
    base = 2
    search = True
    trials = 0
    while search:
        trials += 1
        Success = True
        g = vector((F.random_element(), F.random_element()))
        Success = Success and (g != nanapow(g, [ZZ(p), get_random_bracketing(ZZ(p), base), base]))
        tmp2 = mmult(g, g)
        Success = Success and (tmp2 != nanapow(g, [ZZ(p-1), get_random_bracketing(ZZ(p), base), base]))
        tmp3  = mmult(g, tmp2)
        Success = Success and (tmp3 != nanapow(g, [ZZ(p-2), get_random_bracketing(ZZ(p), base), base]))
        Success = Success and (tmp3 != mmult(tmp2, g))
        Success = Success and (mmult(g, tmp3) != mmult(tmp3, g))
        search = not(Success)
    return(g)

# A procedure that finds a generator of the Sylow q-subquasigroup (\mathbb{E}_{q^2}^*, *)
def find_generator_q():
    global F, p
    g = find_generator_p()
    return( mmult(g,mmult(g,mmult(g,mmult(mmult(g,g),g)))) )

# Intial procedure for generating the random parameters for multi-dimensional entropoids
def Generate_Random_Multidimensional_Entropoid_Parameters(p, Entropoid_dim, rr):
    global aa1, aa3, aa4, aa8, bb1, bb2, bb5, bb7, E_Zero, E_left_unit
    global F, g, g_q
    global m, middle_derangement, Rounds, Leaders
    
    m = Entropoid_dim
    if m < 2:
        print("ERROR: Entropoid dimension should be at least 2!")
        return(-2)
    # Let us fix the global derangement to be the middle one from the cannoical list of all derangements
    D = Derangements(m)
    if m<=8:
        D_cardinality = D.cardinality()
        middle = D.list()[ceil(D_cardinality/2)-1]
        middle_derangement = D(middle).to_permutation()
    elif m == 12:
        middle_derangement = D([1,11,4,8,3,10,5,7,2,12,9,6]).to_permutation()
    elif m == 16:
        middle_derangement = D([1,13,8,10,5,16,14,2,15,12,7,9,6,3,11,4]).to_permutation()    
    else:
        middle_derangement = D.random_element().to_permutation()
    print("The global derangement for multidimensional entropic multiplications is: ", middle_derangement)
    print()
    Rounds = rr
    
    # p = get_fixed_safe_prime(lambda_bits) # or get_random_safe_prime(lambda_bits)
    print("p = ", p)
    print("log_2(p) = ", ceil(log(p, 2)))
    print()
    
    F = GF(p)
    print("Information about the finite field: ", F)
    print()

    # Get some appropriate but random coefficients that define E_{p^2}
    get_random_entropoid_coefficients()
    print("aa1 = ", aa1)
    print("aa3 = ", aa3)
    print("aa4 = ", aa4)
    print("aa8 = ", aa8)
    print("bb1 = ", bb1)
    print("bb2 = ", bb2)
    print("bb5 = ", bb5)
    print("bb7 = ", bb7)
    print()

    # Some of the characteristic elements in the one-dimensional Entropoid 
    print("Some of the characteristic elements in the one-dimensional Entropoid")
    print("E_Zero = ", E_Zero)
    print("E_left_unit = ", E_left_unit)
    E_minus_one = mminus(E_Zero, E_left_unit)
    print("E_minus_one = ", E_minus_one)
    print()
    
    Leaders = [get_random_entropoid_nonzero_element() for i in range(Rounds)]
    print("Leaders = ", Leaders)
    print()
    
    # g is a list of m generators of the multiplicative quasigroup of E_{p^2}
    g = [find_generator_p() for i in range(m)]
    print("g = ", g)
    print()

    # g_q is a list of m generators of the Silow q subquasigroup 
    g_q = [find_generator_q() for i in range(m)]
    print("g_q = ", g_q)
    print()

# This is a computational procedure that gives the same result as 
# we would have evaluated the symbolic bracketing AssocRulesForDifferentBases[base][digit]
def AssocRuleForBaseAndDigit_multi_dim(gg, base, digit):
    j = 0
    tmp = multi_dim_mult(gg, gg)
    if digit == 0:
        while j < base - 2:
            tmp = multi_dim_mult(gg, tmp)
            j += 1
        return(tmp)
    else:
        while j < digit - 1:
            tmp = multi_dim_mult(gg, tmp)
            j += 1
        if j <= base - 2:
            tmp = multi_dim_mult(tmp, gg)
            j += 1
        while j < base - 2:
            tmp = multi_dim_mult(gg, tmp)
            j += 1
        return(tmp)

# This is the non-abelian and non-associative exponentiation of 
# a multidimensional g to the power index nn = [n, n_pattern, base] 
def nanapow_multi_dim(g, nn):
    n = nn[0]
    pattern = nn[1]
    base = nn[2]

    digitss = n.digits(base)

    # Compute equations (39) from the paper
    gg = g
    powlist = [gg]
    for i in range(1, len(pattern)):
        gg = AssocRuleForBaseAndDigit_multi_dim(gg, base, pattern[i])
        powlist.append(gg)

    # find the index of the first non-zero element
    ii = digitss.index(next(filter(lambda x: x!=0, digitss))) 
    
    # Compute equations (40) from the paper
    if digitss[ii] == 1:
        result = powlist[ii]
    else:
        gg = powlist[ii]
        result = AssocRuleForBaseAndDigit_multi_dim(gg, digitss[ii], pattern[ii]%(digitss[ii] - 1))

    # Compute equations (41) from the paper
    ii += 1
    while ii<len(digitss):
        if digitss[ii] != 0:
            if digitss[ii] == 1:
                tmp = powlist[ii]
            else:
                gg = powlist[ii]
                tmp = AssocRuleForBaseAndDigit_multi_dim(gg, digitss[ii], pattern[ii]%(digitss[ii] - 1))
            if pattern[ii-1]%2 == 0:
                result = multi_dim_mult(tmp, result)                
            else:
                result = multi_dim_mult(result, tmp)
        ii += 1
    
    return(result)    
    
import binascii
import hashlib
def concatenate_entropoid_element_and_message(I, M, I_size_in_bytes):
    byte_array = b''
    for i in range(len(I)):
        byte_array = byte_array + int(I[i]).to_bytes(I_size_in_bytes, 'little')
    byte_array = byte_array + bytearray(M.encode())
    return byte_array

def concatenate_multi_dim_entropoid_element_and_message(I, M, I_size_in_bytes):
    byte_array = b''
    for II in I:
        for i in range(len(II)):
            byte_array = byte_array + int(II[i]).to_bytes(I_size_in_bytes, 'little')
    byte_array = byte_array + bytearray(M.encode())
    return byte_array


# Hash to power indices procedures for Signatures01
def Hash512_to_power_index(byte_array, base):
    if not(base in {17, 257}):
        print("ERROR: Base should be either 17 or 257")
        return(-2)
    ss = hashlib.sha512(byte_array).hexdigest()
    ss_first_half = ss[:64]; 
    bb1 = ZZ(int('0x'+ss_first_half,16))
    bb1_in_base = bb1.digits(base); 
    ss_second_half = ss[64:]; 
    bb2 = ZZ(int('0x'+ss_second_half,16))
    bb2_in_base_min_1 = bb2.digits(base - 1)
    bb2_in_base_min_1 = bb2_in_base_min_1[:len(bb1_in_base)]
    return([bb1, bb2_in_base_min_1, base])

def Hash384_to_power_index(byte_array, base):
    if not(base in {17, 257}):
        print("ERROR: Base should be either 17 or 257")
        return(-2)
    ss = hashlib.sha384(byte_array).hexdigest()
    ss_first_half = ss[:48]; 
    bb1 = ZZ(int('0x'+ss_first_half,16))
    bb1_in_base = bb1.digits(base); 
    ss_second_half = ss[48:]; 
    bb2 = ZZ(int('0x'+ss_second_half,16))
    bb2_in_base_min_1 = bb2.digits(base - 1)
    bb2_in_base_min_1 = bb2_in_base_min_1[:len(bb1_in_base)]
    return([bb1, bb2_in_base_min_1, base])

def Hash256_to_power_index(byte_array, base):
    if not(base in {17, 257}):
        print("ERROR: Base should be either 17 or 257")
        return(-2)
    ss = hashlib.sha256(byte_array).hexdigest()
    ss_first_half = ss[:32]; 
    bb1 = ZZ(int('0x'+ss_first_half,16))
    bb1_in_base = bb1.digits(base); 
    ss_second_half = ss[32:]; 
    bb2 = ZZ(int('0x'+ss_second_half,16))
    bb2_in_base_min_1 = bb2.digits(base - 1)
    bb2_in_base_min_1 = bb2_in_base_min_1[:len(bb1_in_base)]
    return([bb1, bb2_in_base_min_1, base])

def GenKey_Signature01_multi_dim(lambda_bits, base, Entropoid_dim, rr):
    global aa1, aa3, aa4, aa8, bb1, bb2, bb5, bb7, E_Zero, E_left_unit
    global F, p, g, g_q, B, PrivateKey, PublicKey, x, y
    global m, middle_derangement, Rounds, Leaders
    
    if not(lambda_bits in {128, 192, 256}):
        print("ERROR: lambda_bits should be either 128 or 192 or 256")
        return(-1)
    if not(base in {17, 257}):
        print("ERROR: Base should be either 17 or 257")
        return(-2)
    
    m = Entropoid_dim
    if m < 2:
        print("ERROR: Entropoid dimension should be at least 2!")
        return(-2)
    # Let us fix the global derangement to be the middle one from the cannoical list of all derangements
    D = Derangements(m)
    if m<=8:
        D_cardinality = D.cardinality()
        middle = D.list()[ceil(D_cardinality/2)-1]
        middle_derangement = D(middle).to_permutation()
    else:
        middle_derangement = D.random_element().to_permutation()
    print("The global derangement for multidimensional entropic multiplications is: ", middle_derangement)
    print()
    Rounds = rr
    
    p = get_fixed_safe_prime(lambda_bits) # or get_random_safe_prime(lambda_bits)
    print("p = ", p)
    print("log_2(p) = ", ceil(log(p, 2)))
    print()
    
    F = GF(p)
    print("Information about the finite field: ", F)
    print()

    # Get some appropriate but random coefficients that define E_p
    get_random_entropoid_coefficients()
    print("aa1 = ", aa1)
    print("aa3 = ", aa3)
    print("aa4 = ", aa4)
    print("aa8 = ", aa8)
    print("bb1 = ", bb1)
    print("bb2 = ", bb2)
    print("bb5 = ", bb5)
    print("bb7 = ", bb7)
    print()

    # Some of the characteristic elements in the Entropoid 
    print("E_Zero = ", E_Zero)
    print("E_left_unit = ", E_left_unit)
    E_minus_one = mminus(E_Zero, E_left_unit)
    print("E_minus_one = ", E_minus_one)
    print()

    Leaders = [get_random_entropoid_nonzero_element() for i in range(Rounds)]
    print("Leaders = ", Leaders)
    print()

    # g is a list of m generators of the multiplicative quasigroup of E_{p^2}
    g = [find_generator_p() for i in range(m)]
    print("g = ", g)
    print()

    # g_q is a list of m generators of the Silow q subquasigroup 
    g_q = [find_generator_q() for i in range(m)]
    print("g_q = ", g_q)
    print()

    # generate a random public parameter B
    # B is a power index
    M = "This is a seed message for fixing the value of the public root."
    if lambda_bits == 128:
        B = Hash256_to_power_index(bytearray(M.encode()), base)
    if lambda_bits == 192:
        B = Hash384_to_power_index(bytearray(M.encode()), base)
    if lambda_bits == 256:
        B = Hash512_to_power_index(bytearray(M.encode()), base)

    print("Public power index B = ", B)
    print()

    # generate the PrivateKey x
    # skip the coordinates of E_Zero
    x = [get_random_entropoid_nonzero_element() for i in range(m)]
    PrivateKey = x
    print("PrivateKey = ", PrivateKey)
    print()
    
    # generate the PublicKey y
    y = nanapow_multi_dim(x, B)
    PublicKey = y
    print("PublicKey = ", PublicKey)
    print()

def Sign_Signature01_multi_dim(PrivateKey, Message, base, lambda_bits):
    global B, m
    # generate a random r
    # skip the coordinates of E_Zero
    r = [get_random_entropoid_nonzero_element() for i in range(m)]
    
    I = nanapow_multi_dim(r, B)
    I_and_Message = concatenate_multi_dim_entropoid_element_and_message(I, Message, lambda_bits//8)
    
    if lambda_bits == 128:
        H = Hash256_to_power_index(I_and_Message, base)
    if lambda_bits == 192:
        H = Hash384_to_power_index(I_and_Message, base)
    if lambda_bits == 256:
        H = Hash512_to_power_index(I_and_Message, base)
        
    s = nanapow_multi_dim(multi_dim_mult(PrivateKey, r), H)
    
    signature = (I, s)
    return signature

def Verify_Signature01_multi_dim(PublicKey, Message, signature, base, lambda_bits):
    global B
    
    I = signature[0]
    I_and_Message = concatenate_multi_dim_entropoid_element_and_message(I, Message, lambda_bits//8)
    
    if lambda_bits == 128:
        H = Hash256_to_power_index(I_and_Message, base)
    if lambda_bits == 192:
        H = Hash384_to_power_index(I_and_Message, base)
    if lambda_bits == 256:
        H = Hash512_to_power_index(I_and_Message, base)
        
    s_to_B = nanapow_multi_dim(signature[1], B)
    y_mult_I_to_H = nanapow_multi_dim(multi_dim_mult(PublicKey, I), H)
    
    if s_to_B == y_mult_I_to_H:
        return True
    else:
        return False

# Hash to power indices for Signatures02
def Hash512_to_power_index_02(byte_array, base):
    if not(base in {17, 257}):
        print("ERROR: Base should be either 17 or 257")
        return(-2)
    ss = hashlib.sha512(byte_array).hexdigest()
    bb_s = ZZ(int('0x'+ss,16))
    bb_s_in_base_min_1 = bb_s.digits(base - 1)
    bb_s_in_base_min_1 = bb_s_in_base_min_1[:len(q.digits(base))]
    return([q, bb_s_in_base_min_1, base])

def Hash384_to_power_index_02(byte_array, base):
    if not(base in {17, 257}):
        print("ERROR: Base should be either 17 or 257")
        return(-2)
    ss = hashlib.sha384(byte_array).hexdigest()
    bb_s = ZZ(int('0x'+ss,16))
    bb_s_in_base_min_1 = bb_s.digits(base - 1)
    bb_s_in_base_min_1 = bb_s_in_base_min_1[:len(q.digits(base))]
    return([q, bb_s_in_base_min_1, base])

def Hash256_to_power_index_02(byte_array, base):
    if not(base in {17, 257}):
        print("ERROR: Base should be either 17 or 257")
        return(-2)
    ss = hashlib.sha256(byte_array).hexdigest()
    bb_s = ZZ(int('0x'+ss,16))
    bb_s_in_base_min_1 = bb_s.digits(base - 1)
    bb_s_in_base_min_1 = bb_s_in_base_min_1[:len(q.digits(base))]
    return([q, bb_s_in_base_min_1, base])

def GenKey_Signature02_multi_dim(lambda_bits, base, Entropoid_dim, rr):
    global aa1, aa3, aa4, aa8, bb1, bb2, bb5, bb7, E_Zero, E_left_unit
    global F, q, p, g, g_q, B, PrivateKey, PublicKey, x, y
    global m, middle_derangement, Rounds, Leaders
    
    if not(lambda_bits in {256, 384, 512}):
        print("ERROR: lambda_bits should be either 256 or 384 or 512")
        return(-1)
    if not(base in {17, 257}):
        print("ERROR: Base should be either 17 or 257")
        return(-2)
    
    m = Entropoid_dim
    if m < 2:
        print("ERROR: Entropoid dimension should be at least 2!")
        return(-2)
    # Let us fix the global derangement to be the middle one from the cannoical list of all derangements
    D = Derangements(m)
    if m<=8:
        D_cardinality = D.cardinality()
        middle = D.list()[ceil(D_cardinality/2)-1]
        middle_derangement = D(middle).to_permutation()
    else:
        middle_derangement = D.random_element().to_permutation()
    print("The global derangement for multidimensional entropic multiplications is: ", middle_derangement)
    print()
    Rounds = rr

    p = get_fixed_safe_prime(lambda_bits) # or get_random_safe_prime(lambda_bits)
    print("p = ", p)
    print("log_2(p) = ", ceil(log(p, 2)))
    print()
    print("q = ", q)
    print("log_2(q) = ", ceil(log(q, 2)))
    print()
    
    F = GF(p)
    print("Information about the finite field: ", F)
    print()

    # Get some appropriate but random coefficients that define E_{p^2}
    get_random_entropoid_coefficients()
    print("aa1 = ", aa1)
    print("aa3 = ", aa3)
    print("aa4 = ", aa4)
    print("aa8 = ", aa8)
    print("bb1 = ", bb1)
    print("bb2 = ", bb2)
    print("bb5 = ", bb5)
    print("bb7 = ", bb7)
    print()

    # Some of the characteristic elements in the Entropoid 
    print("E_Zero = ", E_Zero)
    print("E_left_unit = ", E_left_unit)
    E_minus_one = mminus(E_Zero, E_left_unit)
    print("E_minus_one = ", E_minus_one)
    print()

    Leaders = [get_random_entropoid_nonzero_element() for i in range(Rounds)]
    print("Leaders = ", Leaders)
    print()

    # g is a list of m generators of the multiplicative quasigroup of E_{p^2}
    g = [find_generator_p() for i in range(m)]
    print("g = ", g)
    print()

    # g_q is a list of m generators of the Silow q subquasigroup 
    g_q = [find_generator_q() for i in range(m)]
    print("g_q = ", g_q)
    print()

    # generate a random public parameter B
    # B is a power index
    M = "This is a seed message for fixing the value of the public root."
    if lambda_bits == 256:
        B = Hash256_to_power_index_02(bytearray(M.encode()), base)
    if lambda_bits == 384:
        B = Hash384_to_power_index_02(bytearray(M.encode()), base)
    if lambda_bits == 512:
        B = Hash512_to_power_index_02(bytearray(M.encode()), base)

    print("Public power index B = ", B)
    print()

    # generate the PrivateKey x
    # skip the coordinates of E_Zero
    x = [get_random_entropoid_nonzero_element() for i in range(m)]
    PrivateKey = x
    print("PrivateKey = ", PrivateKey)
    print()
    
    # generate the PublicKey y
    y = nanapow_multi_dim(x, B)
    PublicKey = y
    print("PublicKey = ", PublicKey)
    print()

def Sign_Signature02_multi_dim(PrivateKey, Message, base, lambda_bits):
    global B
    # generate a random r
    # skip the coordinates of E_Zero
    r = [get_random_entropoid_nonzero_element() for i in range(m)]
    
    I = nanapow_multi_dim(r, B)
    I_and_Message = concatenate_multi_dim_entropoid_element_and_message(I, Message, lambda_bits//8)
    
    if lambda_bits == 256:
        H = Hash256_to_power_index_02(I_and_Message, base)
    if lambda_bits == 384:
        H = Hash384_to_power_index_02(I_and_Message, base)
    if lambda_bits == 512:
        H = Hash512_to_power_index_02(I_and_Message, base)
        
    s = nanapow_multi_dim(multi_dim_mult(PrivateKey, r), H)
    
    signature = (I, s)
    return signature

def Verify_Signature02_multi_dim(PublicKey, Message, signature, base, lambda_bits):
    global B
    
    I = signature[0]
    I_and_Message = concatenate_multi_dim_entropoid_element_and_message(I, Message, lambda_bits//8)
    
    if lambda_bits == 256:
        H = Hash256_to_power_index_02(I_and_Message, base)
    if lambda_bits == 384:
        H = Hash384_to_power_index_02(I_and_Message, base)
    if lambda_bits == 512:
        H = Hash512_to_power_index_02(I_and_Message, base)
        
    s_to_B = nanapow_multi_dim(signature[1], B)
    y_mult_I_to_H = nanapow_multi_dim(multi_dim_mult(PublicKey, I), H)

    if s_to_B == y_mult_I_to_H:
        return True
    else:
        return False

# A sanity check that multi_dim_mult(X, Y) is 
# an entropic but not a quasigroup operation

In [22]:
# The results of this code are produced in SageMath 9.2
# To ensure the reproducibility of the results, set a fixed initial seed
# set_random_seed(0)
random.seed(0, version=2)
print("initial seed: ", initial_seed())

m = 2
Rounds = 6

p = 5
Generate_Random_Multidimensional_Entropoid_Parameters(p, m, Rounds)
print()

base_alice = 5
print("base_alice = ", base_alice)
# Alice gets a random power index
Alice = get_random_power_index(base_alice); 
print("Alice = ", Alice)
# Alice produces her public part Ka by calling the procedure nanapow() 
# that uses two parameters g and the power index Alice in order to 
# calculate g  to  the power of Alice
Ka = nanapow_multi_dim(g, Alice)
print("Ka = ", Ka)
print()

base_bob = 5
print("base_bob = ", base_bob)
# Bob gets a random power index
Bob = get_random_power_index(base_bob); 
print("Bob = ", Bob)
# Bob produces his public part Kb by calling the procedure nanapow() 
# that uses two parameters g and the power index Bob in order to 
# calculate g  to the power of Bob
Kb = nanapow_multi_dim(g, Bob)
print("Kb = ", Kb)
print()

# After receiving Kb, Alice computes the shared key Kab
Kab = nanapow_multi_dim(Kb, Alice)
print("Kab = ", Kab)
print()

# After receiving Ka, Bob computes the shared key Kba
Kba = nanapow_multi_dim(Ka, Bob)
print("Kba = ", Kba)
print()

print("The shared keys are the same: ", Kab == Kba)
print()

MMs = set()
YYs = set()
NaturalCollisions = 0
MultiplicativeCollisions = 0

X =  [get_random_entropoid_nonzero_element() for i in range(m)]
attempts = 0
Search = True
quasigroup_search_attempts_limit = 2^ceil(m * log(p-1, 2))

while Search:
    attempts += 1
    if attempts%1000 == 0:
        print('\r' + 'attempts = ' + str(attempts) + '     ', end='')
    if attempts > quasigroup_search_attempts_limit:
        print("Most probably it is a multi-dim quasigroup. STOP!")
        Search = False
        
    Y = [get_random_entropoid_nonzero_element() for i in range(m)]
    yy = [tuple(Y[i]) for i in range(m)]
    yy = {tuple(yy)}
    if YYs.isdisjoint(yy):
        YYs = YYs.union(yy)
        MM = multi_dim_mult(X, Y)
        mm = [tuple(MM[i]) for i in range(m)]
        mm = {tuple(mm)}
        if MMs.isdisjoint(mm):
            MMs = MMs.union(mm)
        else:
            MultiplicativeCollisions += 1
            print("Found collision after ", attempts, " attempts. STOP!")
            print("multi_dim_mult(X, Y) is not a quasigroup operation.")
            Search = False
    else:
        NaturalCollisions += 1
        # print("NaturalCollisions = ", NaturalCollisions, " found after ", attempts, " attempts.")
        if NaturalCollisions > 10:
            print("Most probably it is a multi-dim quasigroup. STOP!")
            Search = False


initial seed:  0
The global derangement for multidimensional entropic multiplications is:  [2, 1]

p =  5
log_2(p) =  3

Information about the finite field:  Finite Field of size 5

aa1 =  0
aa3 =  0
aa4 =  4
aa8 =  4
bb1 =  4
bb2 =  1
bb5 =  0
bb7 =  1

Some of the characteristic elements in the one-dimensional Entropoid
E_Zero =  (0, 4)
E_left_unit =  (1, 3)
E_minus_one =  (4, 0)

Leaders =  [(1, 1), (3, 0), (1, 3), (1, 0), (3, 0), (3, 2)]

g =  [(3, 3), (2, 3)]

g_q =  [(1, 0), (1, 0)]


base_alice =  5
Alice =  [16, [0, 0], 5]
Ka =  [(3, 1), (4, 0)]

base_bob =  5
Bob =  [5, [1, 0], 5]
Kb =  [(4, 0), (2, 2)]

Kab =  [(4, 1), (1, 1)]

Kba =  [(4, 1), (1, 1)]

The shared keys are the same:  True

Found collision after  2  attempts. STOP!
multi_dim_mult(X, Y) is not a quasigroup operation.


In [12]:
# The results of this code are produced in SageMath 9.2
# To ensure the reproducibility of the results, set a fixed initial seed
# set_random_seed(0)
random.seed(0, version=2)
print("initial seed: ", initial_seed())

m = 3
Rounds = 7

p = 5
Generate_Random_Multidimensional_Entropoid_Parameters(p, m, Rounds)
print()

base_alice = 5
print("base_alice = ", base_alice)
# Alice gets a random power index
Alice = get_random_power_index(base_alice); 
print("Alice = ", Alice)
# Alice produces her public part Ka by calling the procedure nanapow() 
# that uses two parameters g and the power index Alice in order to 
# calculate g  to  the power of Alice
Ka = nanapow_multi_dim(g, Alice)
print("Ka = ", Ka)
print()

base_bob = 5
print("base_bob = ", base_bob)
# Bob gets a random power index
Bob = get_random_power_index(base_bob); 
print("Bob = ", Bob)
# Bob produces his public part Kb by calling the procedure nanapow() 
# that uses two parameters g and the power index Bob in order to 
# calculate g  to the power of Bob
Kb = nanapow_multi_dim(g, Bob)
print("Kb = ", Kb)
print()

# After receiving Kb, Alice computes the shared key Kab
Kab = nanapow_multi_dim(Kb, Alice)
print("Kab = ", Kab)
print()

# After receiving Ka, Bob computes the shared key Kba
Kba = nanapow_multi_dim(Ka, Bob)
print("Kba = ", Kba)
print()

print("The shared keys are the same: ", Kab == Kba)
print()

MMs = set()
YYs = set()
NaturalCollisions = 0
MultiplicativeCollisions = 0

X =  [get_random_entropoid_nonzero_element() for i in range(m)]
attempts = 0
Search = True
quasigroup_search_attempts_limit = 2^ceil(m * log(p-1, 2))

while Search:
    attempts += 1
    if attempts%1000 == 0:
        print('\r' + 'attempts = ' + str(attempts) + '     ', end='')
    if attempts > quasigroup_search_attempts_limit:
        print("Most probably it is a multi-dim quasigroup. STOP!")
        Search = False
        
    Y = [get_random_entropoid_nonzero_element() for i in range(m)]
    yy = [tuple(Y[i]) for i in range(m)]
    yy = {tuple(yy)}
    if YYs.isdisjoint(yy):
        YYs = YYs.union(yy)
        MM = multi_dim_mult(X, Y)
        mm = [tuple(MM[i]) for i in range(m)]
        mm = {tuple(mm)}
        if MMs.isdisjoint(mm):
            MMs = MMs.union(mm)
        else:
            MultiplicativeCollisions += 1
            print("Found collision after ", attempts, " attempts. STOP!")
            print("multi_dim_mult(X, Y) is not a quasigroup operation.")
            Search = False
    else:
        NaturalCollisions += 1
        # print("NaturalCollisions = ", NaturalCollisions, " found after ", attempts, " attempts.")
        if NaturalCollisions > 10:
            print("Most probably it is a multi-dim quasigroup. STOP!")
            Search = False


initial seed:  32595716171599108122304808390114346354
The global derangement for multidimensional entropic multiplications is:  [2, 3, 1]

p =  5
log_2(p) =  3

Information about the finite field:  Finite Field of size 5

aa1 =  0
aa3 =  0
aa4 =  0
aa8 =  3
bb1 =  0
bb2 =  0
bb5 =  0
bb7 =  1

Some of the characteristic elements in the one-dimensional Entropoid
E_Zero =  (0, 0)
E_left_unit =  (1, 2)
E_minus_one =  (4, 3)

Leaders =  [(2, 4), (2, 2), (2, 1), (3, 1), (3, 3), (4, 2), (2, 4)]

g =  [(4, 1), (2, 2), (2, 2)]

g_q =  [(1, 3), (4, 2), (1, 3)]


base_alice =  5
Alice =  [36, [3, 3, 2], 5]
Ka =  [(4, 1), (1, 1), (1, 1)]

base_bob =  5
Bob =  [11, [2, 0], 5]
Kb =  [(4, 4), (1, 2), (3, 1)]

Kab =  [(4, 4), (2, 4), (1, 2)]

Kba =  [(4, 4), (2, 4), (1, 2)]

The shared keys are the same:  True

Found collision after  12  attempts. STOP!
multi_dim_mult(X, Y) is not a quasigroup operation.


In [13]:
# The results of this code are produced in SageMath 9.2
# To ensure the reproducibility of the results, set a fixed initial seed
# set_random_seed(0)
random.seed(0, version=2)
print("initial seed: ", initial_seed())

m = 4
Rounds = 7

p = 5
Generate_Random_Multidimensional_Entropoid_Parameters(p, m, Rounds)
print()

base_alice = 5
print("base_alice = ", base_alice)
# Alice gets a random power index
Alice = get_random_power_index(base_alice); 
print("Alice = ", Alice)
# Alice produces her public part Ka by calling the procedure nanapow() 
# that uses two parameters g and the power index Alice in order to 
# calculate g  to  the power of Alice
Ka = nanapow_multi_dim(g, Alice)
print("Ka = ", Ka)
print()

base_bob = 5
print("base_bob = ", base_bob)
# Bob gets a random power index
Bob = get_random_power_index(base_bob); 
print("Bob = ", Bob)
# Bob produces his public part Kb by calling the procedure nanapow() 
# that uses two parameters g and the power index Bob in order to 
# calculate g  to the power of Bob
Kb = nanapow_multi_dim(g, Bob)
print("Kb = ", Kb)
print()

# After receiving Kb, Alice computes the shared key Kab
Kab = nanapow_multi_dim(Kb, Alice)
print("Kab = ", Kab)
print()

# After receiving Ka, Bob computes the shared key Kba
Kba = nanapow_multi_dim(Ka, Bob)
print("Kba = ", Kba)
print()

print("The shared keys are the same: ", Kab == Kba)
print()

MMs = set()
YYs = set()
NaturalCollisions = 0
MultiplicativeCollisions = 0

X =  [get_random_entropoid_nonzero_element() for i in range(m)]
attempts = 0
Search = True
quasigroup_search_attempts_limit = 2^ceil(m * log(p-1, 2))

while Search:
    attempts += 1
    if attempts%1000 == 0:
        print('\r' + 'attempts = ' + str(attempts) + '     ', end='')
    if attempts > quasigroup_search_attempts_limit:
        print("Most probably it is a multi-dim quasigroup. STOP!")
        Search = False
        
    Y = [get_random_entropoid_nonzero_element() for i in range(m)]
    yy = [tuple(Y[i]) for i in range(m)]
    yy = {tuple(yy)}
    if YYs.isdisjoint(yy):
        YYs = YYs.union(yy)
        MM = multi_dim_mult(X, Y)
        mm = [tuple(MM[i]) for i in range(m)]
        mm = {tuple(mm)}
        if MMs.isdisjoint(mm):
            MMs = MMs.union(mm)
        else:
            MultiplicativeCollisions += 1
            print("Found collision after ", attempts, " attempts. STOP!")
            print("multi_dim_mult(X, Y) is not a quasigroup operation.")
            Search = False
    else:
        NaturalCollisions += 1
        # print("NaturalCollisions = ", NaturalCollisions, " found after ", attempts, " attempts.")
        if NaturalCollisions > 10:
            print("Most probably it is a multi-dim quasigroup. STOP!")
            Search = False


initial seed:  32595716171599108122304808390114346354
The global derangement for multidimensional entropic multiplications is:  [3, 1, 4, 2]

p =  5
log_2(p) =  3

Information about the finite field:  Finite Field of size 5

aa1 =  1
aa3 =  3
aa4 =  3
aa8 =  1
bb1 =  0
bb2 =  1
bb5 =  1
bb7 =  2

Some of the characteristic elements in the one-dimensional Entropoid
E_Zero =  (2, 2)
E_left_unit =  (0, 3)
E_minus_one =  (4, 1)

Leaders =  [(3, 0), (0, 4), (3, 4), (1, 1), (4, 1), (3, 0), (3, 0)]

g =  [(4, 4), (4, 0), (0, 0), (1, 1)]

g_q =  [(4, 3), (0, 1), (0, 1), (0, 1)]


base_alice =  5
Alice =  [93, [0, 3, 0], 5]
Ka =  [(1, 1), (3, 3), (4, 0), (0, 0)]

base_bob =  5
Bob =  [52, [3, 1, 2], 5]
Kb =  [(4, 4), (0, 4), (0, 0), (3, 3)]

Kab =  [(1, 1), (1, 1), (4, 0), (4, 4)]

Kba =  [(1, 1), (1, 1), (4, 0), (4, 4)]

The shared keys are the same:  True

Found collision after  9  attempts. STOP!
multi_dim_mult(X, Y) is not a quasigroup operation.


In [14]:
# The results of this code are produced in SageMath 9.2
# To ensure the reproducibility of the results, set a fixed initial seed
# set_random_seed(0)
random.seed(0, version=2)
print("initial seed: ", initial_seed())

m = 8
Rounds = 14

p = 5
Generate_Random_Multidimensional_Entropoid_Parameters(p, m, Rounds)
print()

base_alice = 5
print("base_alice = ", base_alice)
# Alice gets a random power index
Alice = get_random_power_index(base_alice); 
print("Alice = ", Alice)
# Alice produces her public part Ka by calling the procedure nanapow() 
# that uses two parameters g and the power index Alice in order to 
# calculate g  to  the power of Alice
Ka = nanapow_multi_dim(g, Alice)
print("Ka = ", Ka)
print()

base_bob = 5
print("base_bob = ", base_bob)
# Bob gets a random power index
Bob = get_random_power_index(base_bob); 
print("Bob = ", Bob)
# Bob produces his public part Kb by calling the procedure nanapow() 
# that uses two parameters g and the power index Bob in order to 
# calculate g  to the power of Bob
Kb = nanapow_multi_dim(g, Bob)
print("Kb = ", Kb)
print()

# After receiving Kb, Alice computes the shared key Kab
Kab = nanapow_multi_dim(Kb, Alice)
print("Kab = ", Kab)
print()

# After receiving Ka, Bob computes the shared key Kba
Kba = nanapow_multi_dim(Ka, Bob)
print("Kba = ", Kba)
print()

print("The shared keys are the same: ", Kab == Kba)
print()

MMs = set()
YYs = set()
NaturalCollisions = 0
MultiplicativeCollisions = 0

X =  [get_random_entropoid_nonzero_element() for i in range(m)]
attempts = 0
Search = True
quasigroup_search_attempts_limit = 2^ceil(m * log(p-1, 2))

while Search:
    attempts += 1
    if attempts%1000 == 0:
        print('\r' + 'attempts = ' + str(attempts) + '     ', end='')
    if attempts > quasigroup_search_attempts_limit:
        print("Most probably it is a multi-dim quasigroup. STOP!")
        Search = False
        
    Y = [get_random_entropoid_nonzero_element() for i in range(m)]
    yy = [tuple(Y[i]) for i in range(m)]
    yy = {tuple(yy)}
    if YYs.isdisjoint(yy):
        YYs = YYs.union(yy)
        MM = multi_dim_mult(X, Y)
        mm = [tuple(MM[i]) for i in range(m)]
        mm = {tuple(mm)}
        if MMs.isdisjoint(mm):
            MMs = MMs.union(mm)
        else:
            MultiplicativeCollisions += 1
            print("Found collision after ", attempts, " attempts. STOP!")
            print("multi_dim_mult(X, Y) is not a quasigroup operation.")
            Search = False
    else:
        NaturalCollisions += 1
        # print("NaturalCollisions = ", NaturalCollisions, " found after ", attempts, " attempts.")
        if NaturalCollisions > 10:
            print("Most probably it is a multi-dim quasigroup. STOP!")
            Search = False


initial seed:  32595716171599108122304808390114346354
The global derangement for multidimensional entropic multiplications is:  [6, 1, 5, 3, 7, 2, 8, 4]

p =  5
log_2(p) =  3

Information about the finite field:  Finite Field of size 5

aa1 =  2
aa3 =  1
aa4 =  0
aa8 =  2
bb1 =  0
bb2 =  0
bb5 =  3
bb7 =  1

Some of the characteristic elements in the one-dimensional Entropoid
E_Zero =  (2, 0)
E_left_unit =  (3, 3)
E_minus_one =  (1, 2)

Leaders =  [(3, 2), (0, 1), (0, 4), (4, 1), (4, 3), (4, 1), (0, 3), (0, 4), (4, 3), (1, 2), (3, 4), (0, 2), (4, 4), (4, 1)]

g =  [(4, 2), (3, 1), (1, 4), (0, 3), (4, 3), (1, 4), (0, 3), (1, 1)]

g_q =  [(1, 3), (3, 2), (1, 3), (3, 2), (1, 3), (1, 3), (3, 2), (3, 2)]


base_alice =  5
Alice =  [55885, [1, 2, 3, 3, 3, 1, 0], 5]
Ka =  [(1, 4), (4, 2), (4, 2), (0, 4), (3, 3), (0, 1), (0, 4), (0, 4)]

base_bob =  5
Bob =  [32, [1, 2, 2], 5]
Kb =  [(3, 1), (3, 2), (3, 4), (0, 2), (3, 2), (0, 3), (3, 4), (3, 1)]

Kab =  [(4, 3), (1, 2), (4, 2), (4, 1), (1, 4)

# Experiments with multi-dimensional entropoid Diffie-Hellman key exchange

In [17]:
# The results of this code are produced in SageMath 9.2
# To ensure the reproducibility of the results, set a fixed initial seed
# set_random_seed(0)
random.seed(0, version=2)
print("initial seed: ", initial_seed())

# p is the 4-th Fermat prime number 2^(2^4) + 1
# Thus the original Entropid structure E^* would have 2^16 elements.
# We can describe every element (x1, x2) in E^* with 32 bits
p = 2^(2^4) + 1

# for generating a magma (lelft quasigroup) with ~ 2^256 elements
# we need m x 32 = 256
m = 8
Rounds = 21


Generate_Random_Multidimensional_Entropoid_Parameters(p, m, Rounds)
print()

base_alice = 17
print("base_alice = ", base_alice)
# Alice gets a random power index
Alice = get_random_power_index(base_alice); 
print("Alice = ", Alice)
# Alice produces her public part Ka by calling the procedure nanapow() 
# that uses two parameters g and the power index Alice in order to 
# calculate g  to  the power of Alice
Ka = nanapow_multi_dim(g, Alice)
print("Ka = ", Ka)
print()

base_bob = 17
print("base_bob = ", base_bob)
# Bob gets a random power index
Bob = get_random_power_index(base_bob); 
print("Bob = ", Bob)
# Bob produces his public part Kb by calling the procedure nanapow() 
# that uses two parameters g and the power index Bob in order to 
# calculate g  to the power of Bob
Kb = nanapow_multi_dim(g, Bob)
print("Kb = ", Kb)
print()

# After receiving Kb, Alice computes the shared key Kab
Kab = nanapow_multi_dim(Kb, Alice)
print("Kab = ", Kab)
print()

# After receiving Ka, Bob computes the shared key Kba
Kba = nanapow_multi_dim(Ka, Bob)
print("Kba = ", Kba)
print()

print("The shared keys are the same: ", Kab == Kba)
print()


initial seed:  32595716171599108122304808390114346354
The global derangement for multidimensional entropic multiplications is:  [6, 1, 5, 3, 7, 2, 8, 4]

p =  65537
log_2(p) =  17

Information about the finite field:  Finite Field of size 65537

aa1 =  10253
aa3 =  43133
aa4 =  2447
aa8 =  38191
bb1 =  27912
bb2 =  64348
bb5 =  7699
bb7 =  38597

Some of the characteristic elements in the one-dimensional Entropoid
E_Zero =  (49805, 55215)
E_left_unit =  (38111, 56478)
E_minus_one =  (61499, 53952)

Leaders =  [(38060, 6366), (28368, 19139), (43969, 54074), (16348, 11923), (34346, 60299), (59505, 20748), (58040, 42572), (6121, 31189), (13111, 46978), (61172, 50786), (4672, 32427), (13576, 36450), (45284, 38879), (26136, 17224), (19885, 34603), (23899, 61535), (38119, 17365), (37890, 40697), (64477, 42498), (43169, 44952), (54759, 8214)]

g =  [(27506, 8790), (6252, 38530), (668, 59539), (2321, 65474), (61529, 56250), (61750, 36184), (55996, 25725), (34021, 36462)]

g_q =  [(9668, 47376)

In [18]:
# The results of this code are produced in SageMath 9.2
# To ensure the reproducibility of the results, set a fixed initial seed
# set_random_seed(0)
random.seed(0, version=2)
print("initial seed: ", initial_seed())

# p is the 4-th Fermat prime number 2^(2^4) + 1
# Thus the original Entropid structure E^* would have 2^16 elements.
# We can describe every element (x1, x2) in E^* with 32 bits
p = 2^(2^4) + 1

# for generating a magma (lelft quasigroup) with ~ 2^384 elements
# we need m x 32 = 384
m = 12
Rounds = 28


Generate_Random_Multidimensional_Entropoid_Parameters(p, m, Rounds)
print()

base_alice = 17
print("base_alice = ", base_alice)
# Alice gets a random power index
Alice = get_random_power_index(base_alice); 
print("Alice = ", Alice)
# Alice produces her public part Ka by calling the procedure nanapow() 
# that uses two parameters g and the power index Alice in order to 
# calculate g  to  the power of Alice
Ka = nanapow_multi_dim(g, Alice)
print("Ka = ", Ka)
print()

base_bob = 17
print("base_bob = ", base_bob)
# Bob gets a random power index
Bob = get_random_power_index(base_bob); 
print("Bob = ", Bob)
# Bob produces his public part Kb by calling the procedure nanapow() 
# that uses two parameters g and the power index Bob in order to 
# calculate g  to the power of Bob
Kb = nanapow_multi_dim(g, Bob)
print("Kb = ", Kb)
print()

# After receiving Kb, Alice computes the shared key Kab
Kab = nanapow_multi_dim(Kb, Alice)
print("Kab = ", Kab)
print()

# After receiving Ka, Bob computes the shared key Kba
Kba = nanapow_multi_dim(Ka, Bob)
print("Kba = ", Kba)
print()

print("The shared keys are the same: ", Kab == Kba)
print()


initial seed:  32595716171599108122304808390114346354
The global derangement for multidimensional entropic multiplications is:  [1, 11, 4, 8, 3, 10, 5, 7, 2, 12, 9, 6]

p =  65537
log_2(p) =  17

Information about the finite field:  Finite Field of size 65537

aa1 =  43764
aa3 =  41733
aa4 =  23849
aa8 =  4861
bb1 =  11978
bb2 =  36161
bb5 =  28389
bb7 =  55040

Some of the characteristic elements in the one-dimensional Entropoid
E_Zero =  (45386, 37570)
E_left_unit =  (29534, 18250)
E_minus_one =  (61238, 56890)

Leaders =  [(29916, 34375), (38235, 19500), (29623, 26722), (44873, 7575), (23273, 32396), (30996, 37745), (39866, 60806), (61181, 46216), (4373, 61491), (40850, 53073), (26909, 57522), (18850, 105), (12708, 10376), (38705, 13530), (38697, 27529), (14808, 39424), (43204, 38021), (18734, 53030), (64549, 60473), (63661, 38957), (52604, 49713), (30029, 45556), (45013, 17095), (64659, 40730), (18118, 11468), (13031, 58266), (50, 21854), (54090, 47639)]

g =  [(4746, 58757), (4103

In [19]:
# The results of this code are produced in SageMath 9.2
# To ensure the reproducibility of the results, set a fixed initial seed
# set_random_seed(0)
random.seed(0, version=2)
print("initial seed: ", initial_seed())

# p is the 4-th Fermat prime number 2^(2^4) + 1
# Thus the original Entropid structure E^* would have 2^16 elements.
# We can describe every element (x1, x2) in E^* with 32 bits
p = 2^(2^4) + 1

# for generating a magma (lelft quasigroup) with ~ 2^512 elements
# we need m x 32 = 512
m = 16
Rounds = 28


Generate_Random_Multidimensional_Entropoid_Parameters(p, m, Rounds)
print()

base_alice = 17
print("base_alice = ", base_alice)
# Alice gets a random power index
Alice = get_random_power_index(base_alice); 
print("Alice = ", Alice)
# Alice produces her public part Ka by calling the procedure nanapow() 
# that uses two parameters g and the power index Alice in order to 
# calculate g  to  the power of Alice
Ka = nanapow_multi_dim(g, Alice)
print("Ka = ", Ka)
print()

base_bob = 17
print("base_bob = ", base_bob)
# Bob gets a random power index
Bob = get_random_power_index(base_bob); 
print("Bob = ", Bob)
# Bob produces his public part Kb by calling the procedure nanapow() 
# that uses two parameters g and the power index Bob in order to 
# calculate g  to the power of Bob
Kb = nanapow_multi_dim(g, Bob)
print("Kb = ", Kb)
print()

# After receiving Kb, Alice computes the shared key Kab
Kab = nanapow_multi_dim(Kb, Alice)
print("Kab = ", Kab)
print()

# After receiving Ka, Bob computes the shared key Kba
Kba = nanapow_multi_dim(Ka, Bob)
print("Kba = ", Kba)
print()

print("The shared keys are the same: ", Kab == Kba)
print()


initial seed:  32595716171599108122304808390114346354
The global derangement for multidimensional entropic multiplications is:  [1, 13, 8, 10, 5, 16, 14, 2, 15, 12, 7, 9, 6, 3, 11, 4]

p =  65537
log_2(p) =  17

Information about the finite field:  Finite Field of size 65537

aa1 =  34238
aa3 =  65399
aa4 =  5948
aa8 =  16924
bb1 =  52647
bb2 =  56309
bb5 =  65090
bb7 =  34873

Some of the characteristic elements in the one-dimensional Entropoid
E_Zero =  (28261, 31862)
E_left_unit =  (22313, 41090)
E_minus_one =  (34209, 22634)

Leaders =  [(55599, 32644), (13507, 28715), (37152, 47218), (43645, 39959), (36258, 31884), (43001, 3932), (58349, 7170), (51029, 57674), (43058, 55879), (23754, 45796), (61184, 61686), (59646, 14789), (7880, 56379), (26430, 55380), (752, 51560), (8331, 34459), (25323, 26067), (56456, 47491), (56733, 25972), (33053, 61173), (58747, 59730), (24688, 64362), (15265, 34092), (13588, 32193), (47011, 60510), (21422, 42709), (4796, 22584), (8686, 22702)]

g =  [(4358

# Experiments with digital signatures 01

In [30]:
# The results of this code are produced in SageMath 9.2
# To ensure the reproducibility of the results, set a fixed initial seed
set_random_seed(0)
random.seed(0, version=2)
print("initial seed: ", initial_seed())

m = 2
Rounds = 14

lambda_bits = 128
base = 17
GenKey_Signature01_multi_dim(lambda_bits, base, m, Rounds)

print()
Message = "Try to sign this message!"
print("Signing the message: ", Message)
signature = Sign_Signature01_multi_dim(PrivateKey, Message, base, lambda_bits)
print("signature = ", signature)
print("Verify: ", Verify_Signature01_multi_dim(PublicKey, Message, signature, base, lambda_bits))
print()
# Corrupt the Message
Message = "Try to sign this message"
print("An attampt to verify a signature of a corrupted message")
print("Verify: ", Verify_Signature01_multi_dim(PublicKey, Message, signature, base, lambda_bits))

initial seed:  0
The global derangement for multidimensional entropic multiplications is:  [2, 1]

p =  255211775190703847597530955573826162347
log_2(p) =  128

Information about the finite field:  Finite Field of size 255211775190703847597530955573826162347

aa1 =  76196257025066871002891471619848650286
aa3 =  222398418873342498392506793217273317643
aa4 =  241322191999219874657044597267756778501
aa8 =  178720374391503507560897272085794393770
bb1 =  47717732877487248530043326597560953714
bb2 =  61733507447498311892063876037630235726
bb5 =  247856823686916680700123131434371243080
bb7 =  27228823810010487136687635290782267614

E_Zero =  (25958627203386039978290716591117649049, 211647247068710178442880791600586184585)
E_left_unit =  (174395086300108117424968928287131469871, 150946712368694434305233963210010197064)
E_minus_one =  (132733943297367810129143460468929990574, 17136006578022074982996664417336009759)

Leaders =  [(51470548742587486727608428014675873429, 96748678266432083440352147

In [31]:
# The results of this code are produced in SageMath 9.2
# To ensure the reproducibility of the results, set a fixed initial seed
set_random_seed(0)
random.seed(0, version=2)
print("initial seed: ", initial_seed())

m = 4
Rounds = 14

lambda_bits = 128
base = 17
GenKey_Signature01_multi_dim(lambda_bits, base, m, Rounds)

print()
Message = "Try to sign this message!"
print("Signing the message: ", Message)
signature = Sign_Signature01_multi_dim(PrivateKey, Message, base, lambda_bits)
print("signature = ", signature)
print("Verify: ", Verify_Signature01_multi_dim(PublicKey, Message, signature, base, lambda_bits))
print()
# Corrupt the Message
Message = "Try to sign this message"
print("An attampt to verify a signature of a corrupted message")
print("Verify: ", Verify_Signature01_multi_dim(PublicKey, Message, signature, base, lambda_bits))

initial seed:  0
The global derangement for multidimensional entropic multiplications is:  [3, 1, 4, 2]

p =  255211775190703847597530955573826162347
log_2(p) =  128

Information about the finite field:  Finite Field of size 255211775190703847597530955573826162347

aa1 =  76196257025066871002891471619848650286
aa3 =  222398418873342498392506793217273317643
aa4 =  241322191999219874657044597267756778501
aa8 =  178720374391503507560897272085794393770
bb1 =  47717732877487248530043326597560953714
bb2 =  61733507447498311892063876037630235726
bb5 =  247856823686916680700123131434371243080
bb7 =  27228823810010487136687635290782267614

E_Zero =  (25958627203386039978290716591117649049, 211647247068710178442880791600586184585)
E_left_unit =  (174395086300108117424968928287131469871, 150946712368694434305233963210010197064)
E_minus_one =  (132733943297367810129143460468929990574, 17136006578022074982996664417336009759)

Leaders =  [(51470548742587486727608428014675873429, 96748678266432083440

In [32]:
# The results of this code are produced in SageMath 9.2
# To ensure the reproducibility of the results, set a fixed initial seed
set_random_seed(0)
random.seed(0, version=2)
print("initial seed: ", initial_seed())

m = 2
Rounds = 14

lambda_bits = 192
base = 17
GenKey_Signature01_multi_dim(lambda_bits, base, m, Rounds)

print()
Message = "Try to sign this message!"
print("Signing the message: ", Message)
signature = Sign_Signature01_multi_dim(PrivateKey, Message, base, lambda_bits)
print("signature = ", signature)
print("Verify: ", Verify_Signature01_multi_dim(PublicKey, Message, signature, base, lambda_bits))
print()
# Corrupt the Message
Message = "Try to sign this message"
print("An attampt to verify a signature of a corrupted message")
print("Verify: ", Verify_Signature01_multi_dim(PublicKey, Message, signature, base, lambda_bits))

initial seed:  0
The global derangement for multidimensional entropic multiplications is:  [2, 1]

p =  4707826301540010572876842067405749812076766583348025913783
log_2(p) =  192

Information about the finite field:  Finite Field of size 4707826301540010572876842067405749812076766583348025913783

aa1 =  257405322579552167145111504184189350941678348657606363000
aa3 =  119532791761269064716056035369728457738265053964404214027
aa4 =  739437136086943117194679493097867279546663219437537419926
aa8 =  3296809007157619640119308770869998958606195085103878511269
bb1 =  1271238259397074869634643961725054659706124524993994915864
bb2 =  2806677724762809107594599379975401118512734879194091885646
bb5 =  4599163888442026094155062442360406257983778255665643166463
bb7 =  949464039987904334513186654173522437107012951521210331273

E_Zero =  (2674838327407532648726594500168436242421616629939967512484, 1660530161738285992366893199821047810162372675981459243468)
E_left_unit =  (366547362505620205879025426766

In [33]:
# The results of this code are produced in SageMath 9.2
# To ensure the reproducibility of the results, set a fixed initial seed
set_random_seed(0)
random.seed(0, version=2)
print("initial seed: ", initial_seed())

m = 4
Rounds = 14

lambda_bits = 192
base = 17
GenKey_Signature01_multi_dim(lambda_bits, base, m, Rounds)

print()
Message = "Try to sign this message!"
print("Signing the message: ", Message)
signature = Sign_Signature01_multi_dim(PrivateKey, Message, base, lambda_bits)
print("signature = ", signature)
print("Verify: ", Verify_Signature01_multi_dim(PublicKey, Message, signature, base, lambda_bits))
print()
# Corrupt the Message
Message = "Try to sign this message"
print("An attampt to verify a signature of a corrupted message")
print("Verify: ", Verify_Signature01_multi_dim(PublicKey, Message, signature, base, lambda_bits))

initial seed:  0
The global derangement for multidimensional entropic multiplications is:  [3, 1, 4, 2]

p =  4707826301540010572876842067405749812076766583348025913783
log_2(p) =  192

Information about the finite field:  Finite Field of size 4707826301540010572876842067405749812076766583348025913783

aa1 =  257405322579552167145111504184189350941678348657606363000
aa3 =  119532791761269064716056035369728457738265053964404214027
aa4 =  739437136086943117194679493097867279546663219437537419926
aa8 =  3296809007157619640119308770869998958606195085103878511269
bb1 =  1271238259397074869634643961725054659706124524993994915864
bb2 =  2806677724762809107594599379975401118512734879194091885646
bb5 =  4599163888442026094155062442360406257983778255665643166463
bb7 =  949464039987904334513186654173522437107012951521210331273

E_Zero =  (2674838327407532648726594500168436242421616629939967512484, 1660530161738285992366893199821047810162372675981459243468)
E_left_unit =  (366547362505620205879025

In [34]:
# The results of this code are produced in SageMath 9.2
# To ensure the reproducibility of the results, set a fixed initial seed
set_random_seed(0)
random.seed(0, version=2)
print("initial seed: ", initial_seed())

m = 2
Rounds = 7

lambda_bits = 256
base = 17
GenKey_Signature01_multi_dim(lambda_bits, base, m, Rounds)

print()
Message = "Try to sign this message!"
print("Signing the message: ", Message)
signature = Sign_Signature01_multi_dim(PrivateKey, Message, base, lambda_bits)
print("signature = ", signature)
print("Verify: ", Verify_Signature01_multi_dim(PublicKey, Message, signature, base, lambda_bits))
print()
# Corrupt the Message
Message = "Try to sign this message"
print("An attampt to verify a signature of a corrupted message")
print("Verify: ", Verify_Signature01_multi_dim(PublicKey, Message, signature, base, lambda_bits))

initial seed:  0
The global derangement for multidimensional entropic multiplications is:  [2, 1]

p =  86844066927987146567678238756515930889952488499230423029593188005934847271147
log_2(p) =  256

Information about the finite field:  Finite Field of size 86844066927987146567678238756515930889952488499230423029593188005934847271147

aa1 =  32020853807654887644334957222306269398498608370866698553183453753385508071789
aa3 =  21006824032566107844541320689058119045737974467270935413688009986168488070826
aa4 =  78901668574955584791111916221370791050852265697346349228460454742358577919791
aa8 =  17514520152847203018279441394225361894014762419869662416889631828284746070238
bb1 =  21504609816581240890771596944610981247772392172380469982872574919132312646024
bb2 =  25223174955288415702340049551314795160644138670364684787245633274934513695975
bb5 =  51809049454113147465743186155015416837084822644379520043428264433478357770134
bb7 =  54522689072505696568590869193235206153532724699456527123048120

In [35]:
# The results of this code are produced in SageMath 9.2
# To ensure the reproducibility of the results, set a fixed initial seed
set_random_seed(0)
random.seed(0, version=2)
print("initial seed: ", initial_seed())

m = 4
Rounds = 14

lambda_bits = 256
base = 17
GenKey_Signature01_multi_dim(lambda_bits, base, m, Rounds)

print()
Message = "Try to sign this message!"
print("Signing the message: ", Message)
signature = Sign_Signature01_multi_dim(PrivateKey, Message, base, lambda_bits)
print("signature = ", signature)
print("Verify: ", Verify_Signature01_multi_dim(PublicKey, Message, signature, base, lambda_bits))
print()
# Corrupt the Message
Message = "Try to sign this message"
print("An attampt to verify a signature of a corrupted message")
print("Verify: ", Verify_Signature01_multi_dim(PublicKey, Message, signature, base, lambda_bits))

initial seed:  0
The global derangement for multidimensional entropic multiplications is:  [3, 1, 4, 2]

p =  86844066927987146567678238756515930889952488499230423029593188005934847271147
log_2(p) =  256

Information about the finite field:  Finite Field of size 86844066927987146567678238756515930889952488499230423029593188005934847271147

aa1 =  32020853807654887644334957222306269398498608370866698553183453753385508071789
aa3 =  21006824032566107844541320689058119045737974467270935413688009986168488070826
aa4 =  78901668574955584791111916221370791050852265697346349228460454742358577919791
aa8 =  17514520152847203018279441394225361894014762419869662416889631828284746070238
bb1 =  21504609816581240890771596944610981247772392172380469982872574919132312646024
bb2 =  25223174955288415702340049551314795160644138670364684787245633274934513695975
bb5 =  51809049454113147465743186155015416837084822644379520043428264433478357770134
bb7 =  54522689072505696568590869193235206153532724699456527123

# Experiments with digital signatures 02

In [36]:
# The results of this code are produced in SageMath 9.2
# To ensure the reproducibility of the results, set a fixed initial seed
set_random_seed(0)
random.seed(0, version=2)
print("initial seed: ", initial_seed())

m = 2
Rounds = 7

lambda_bits = 256
base = 17
GenKey_Signature02_multi_dim(lambda_bits, base, m, Rounds)

print()
Message = "Try to sign this message!"
print("Signing the message: ", Message)
signature = Sign_Signature02_multi_dim(PrivateKey, Message, base, lambda_bits)
print("signature = ", signature)
print("Verify: ", Verify_Signature02_multi_dim(PublicKey, Message, signature, base, lambda_bits))
print()
# Corrupt the Message
Message = "Try to sign this message"
print("An attampt to verify a signature of a corrupted message")
print("Verify: ", Verify_Signature02_multi_dim(PublicKey, Message, signature, base, lambda_bits))

initial seed:  0
The global derangement for multidimensional entropic multiplications is:  [2, 1]

p =  86844066927987146567678238756515930889952488499230423029593188005934847271147
log_2(p) =  256

q =  43422033463993573283839119378257965444976244249615211514796594002967423635959
log_2(q) =  255

Information about the finite field:  Finite Field of size 86844066927987146567678238756515930889952488499230423029593188005934847271147

aa1 =  32020853807654887644334957222306269398498608370866698553183453753385508071789
aa3 =  21006824032566107844541320689058119045737974467270935413688009986168488070826
aa4 =  78901668574955584791111916221370791050852265697346349228460454742358577919791
aa8 =  17514520152847203018279441394225361894014762419869662416889631828284746070238
bb1 =  21504609816581240890771596944610981247772392172380469982872574919132312646024
bb2 =  25223174955288415702340049551314795160644138670364684787245633274934513695975
bb5 =  51809049454113147465743186155015416837084822644

In [37]:
# The results of this code are produced in SageMath 9.2
# To ensure the reproducibility of the results, set a fixed initial seed
set_random_seed(0)
random.seed(0, version=2)
print("initial seed: ", initial_seed())

m = 4
Rounds = 14

lambda_bits = 256
base = 17
GenKey_Signature02_multi_dim(lambda_bits, base, m, Rounds)

print()
Message = "Try to sign this message!"
print("Signing the message: ", Message)
signature = Sign_Signature02_multi_dim(PrivateKey, Message, base, lambda_bits)
print("signature = ", signature)
print("Verify: ", Verify_Signature02_multi_dim(PublicKey, Message, signature, base, lambda_bits))
print()
# Corrupt the Message
Message = "Try to sign this message"
print("An attampt to verify a signature of a corrupted message")
print("Verify: ", Verify_Signature02_multi_dim(PublicKey, Message, signature, base, lambda_bits))

initial seed:  0
The global derangement for multidimensional entropic multiplications is:  [3, 1, 4, 2]

p =  86844066927987146567678238756515930889952488499230423029593188005934847271147
log_2(p) =  256

q =  43422033463993573283839119378257965444976244249615211514796594002967423635959
log_2(q) =  255

Information about the finite field:  Finite Field of size 86844066927987146567678238756515930889952488499230423029593188005934847271147

aa1 =  32020853807654887644334957222306269398498608370866698553183453753385508071789
aa3 =  21006824032566107844541320689058119045737974467270935413688009986168488070826
aa4 =  78901668574955584791111916221370791050852265697346349228460454742358577919791
aa8 =  17514520152847203018279441394225361894014762419869662416889631828284746070238
bb1 =  21504609816581240890771596944610981247772392172380469982872574919132312646024
bb2 =  25223174955288415702340049551314795160644138670364684787245633274934513695975
bb5 =  51809049454113147465743186155015416837084

Verify:  False


In [18]:
# The results of this code are produced in SageMath 9.2
# To ensure the reproducibility of the results, set a fixed initial seed
set_random_seed(0)
random.seed(0, version=2)
print("initial seed: ", initial_seed())

m = 2
Rounds = 32

lambda_bits = 384
base = 17
GenKey_Signature02_multi_dim(lambda_bits, base, m, Rounds)

print()
Message = "Try to sign this message!"
print("Signing the message: ", Message)
signature = Sign_Signature02_multi_dim(PrivateKey, Message, base, lambda_bits)
print("signature = ", signature)
print("Verify: ", Verify_Signature02_multi_dim(PublicKey, Message, signature, base, lambda_bits))
print()
# Corrupt the Message
Message = "Try to sign this message"
print("An attampt to verify a signature of a corrupted message")
print("Verify: ", Verify_Signature02_multi_dim(PublicKey, Message, signature, base, lambda_bits))

initial seed:  0
The global derangement for multidimensional entropic multiplications is:  [2, 1]

p =  29551504647295859409209280075107710353809804452849085000961220053184291328622907958560699691163686730604970992766987
log_2(p) =  384

q =  14775752323647929704604640037553855176904902226424542500480610026592145664311453979280349845581843365302485496383537
log_2(q) =  383

Information about the finite field:  Finite Field of size 29551504647295859409209280075107710353809804452849085000961220053184291328622907958560699691163686730604970992766987

aa1 =  7582394856132617620350301691287562681665178319115996216711488798994296321260008236339887422691230485947234341760057
aa3 =  20694405540067534286571407614852013949226916019336790190813868190978548966530225161940296844908863294027036466039051
aa4 =  28404507750296719480401111253101391650589452796426587072246545895132703299002258997178724078203659396904636222958928
aa8 =  595988237309532315740388168846994021514742101893720676337673154601540

In [38]:
# The results of this code are produced in SageMath 9.2
# To ensure the reproducibility of the results, set a fixed initial seed
set_random_seed(0)
random.seed(0, version=2)
print("initial seed: ", initial_seed())

m = 4
Rounds = 14

lambda_bits = 384
base = 17
GenKey_Signature02_multi_dim(lambda_bits, base, m, Rounds)

print()
Message = "Try to sign this message!"
print("Signing the message: ", Message)
signature = Sign_Signature02_multi_dim(PrivateKey, Message, base, lambda_bits)
print("signature = ", signature)
print("Verify: ", Verify_Signature02_multi_dim(PublicKey, Message, signature, base, lambda_bits))
print()
# Corrupt the Message
Message = "Try to sign this message"
print("An attampt to verify a signature of a corrupted message")
print("Verify: ", Verify_Signature02_multi_dim(PublicKey, Message, signature, base, lambda_bits))

initial seed:  0
The global derangement for multidimensional entropic multiplications is:  [3, 1, 4, 2]

p =  29551504647295859409209280075107710353809804452849085000961220053184291328622907958560699691163686730604970992766987
log_2(p) =  384

q =  14775752323647929704604640037553855176904902226424542500480610026592145664311453979280349845581843365302485496383537
log_2(q) =  383

Information about the finite field:  Finite Field of size 29551504647295859409209280075107710353809804452849085000961220053184291328622907958560699691163686730604970992766987

aa1 =  7582394856132617620350301691287562681665178319115996216711488798994296321260008236339887422691230485947234341760057
aa3 =  20694405540067534286571407614852013949226916019336790190813868190978548966530225161940296844908863294027036466039051
aa4 =  28404507750296719480401111253101391650589452796426587072246545895132703299002258997178724078203659396904636222958928
aa8 =  595988237309532315740388168846994021514742101893720676337673154

PublicKey =  [(1921071506111567069165766088478189353973701338872829293005985559285489504555907279814814669623689400362436994471651, 9284291533738471836394506597543266825888897622104978750223601650747599199151816806958370397181576316410629254173154), (5066188109592058098219648539995405320556203928492230217558622906224175208823283186863879126383880128119993421517791, 24006134094431226163292121625570481306560717008371708604781891958671843610627865982630168597137407468261754043450054), (15209976761108195409569041765555137434491158036918911678123798531017039740872519680308955908000195847944336966715380, 12036605924201958940467219724227703524375842942046164502174990939015643780581835501460769358814593943389301080904137), (5483489422220338835875671199829307138930958446800468375468995121525198077595172057957175195235723116915597947598650, 29334434238446191292606642921506147024728088057893966512618253028533707882144594114341806104865705560463619198181951)]


Signing the message:  Try to sign th

In [39]:
# The results of this code are produced in SageMath 9.2
# To ensure the reproducibility of the results, set a fixed initial seed
set_random_seed(0)
random.seed(0, version=2)
print("initial seed: ", initial_seed())

m = 2
Rounds = 7

lambda_bits = 512
base = 17
GenKey_Signature02_multi_dim(lambda_bits, base, m, Rounds)

print()
Message = "Try to sign this message!"
print("Signing the message: ", Message)
signature = Sign_Signature02_multi_dim(PrivateKey, Message, base, lambda_bits)
print("signature = ", signature)
print("Verify: ", Verify_Signature02_multi_dim(PublicKey, Message, signature, base, lambda_bits))
print()
# Corrupt the Message
Message = "Try to sign this message"
print("An attampt to verify a signature of a corrupted message")
print("Verify: ", Verify_Signature02_multi_dim(PublicKey, Message, signature, base, lambda_bits))

initial seed:  0
The global derangement for multidimensional entropic multiplications is:  [2, 1]

p =  10055855947456947824680518748654384595609524365444295033292671082791323022555160232601405723625177570767523893639864538140315412108959927459825236754597199
log_2(p) =  512

q =  5027927973728473912340259374327192297804762182722147516646335541395661511277580116300702861812588785383761946819932269070157706054479963729912618377298809
log_2(q) =  511

Information about the finite field:  Finite Field of size 10055855947456947824680518748654384595609524365444295033292671082791323022555160232601405723625177570767523893639864538140315412108959927459825236754597199

aa1 =  5083521238499181616107103435540117463555863868499725717345286618378307579761303457915289965842449989320867780251139340372938505409275428692727806563961170
aa3 =  2432424042971493215259752716409360521732123369897594983538095158510825326037876699129932315236342603157409792578609891994907734721051329531278165610547467
aa4 =  

signature =  ([(379505223696594675673705107440272121583026329395358314283287063483792234220707828783067910072355745198786899648017681897959796665401067394154698669527036, 8511617752331097036199412644547115991054961976074072619413760532979378180377646468889976048619496015359656153417569886130864767405529418226644448637852919), (3417505708388477915670703578139691368671095468109321525190875375818296672510432105451171260269484384596462372587309499428929834553922566499226431473275493, 8378687311247839756805985672657512187324418980607773415500784850352132219551420230744609600766158035642496814684714809049992297816900001138070525354168633)], [(7698386228792816128001200068073561436601432669393397599431532079644338766337917444787408246570498008836630029563580303103000385731176559446725843092811344, 8201300628481074916960446865436034165633038914186031217442743666092768453496156751818983277391890525493375968122258820843556717769167254497363743400425290), (70557255935590965452523190214773069791298

In [21]:
# The results of this code are produced in SageMath 9.2
# To ensure the reproducibility of the results, set a fixed initial seed
set_random_seed(0)
random.seed(0, version=2)
print("initial seed: ", initial_seed())

m = 4
Rounds = 14

lambda_bits = 512
base = 17
GenKey_Signature02_multi_dim(lambda_bits, base, m, Rounds)

print()
Message = "Try to sign this message!"
print("Signing the message: ", Message)
signature = Sign_Signature02_multi_dim(PrivateKey, Message, base, lambda_bits)
print("signature = ", signature)
print("Verify: ", Verify_Signature02_multi_dim(PublicKey, Message, signature, base, lambda_bits))
print()
# Corrupt the Message
Message = "Try to sign this message"
print("An attampt to verify a signature of a corrupted message")
print("Verify: ", Verify_Signature02_multi_dim(PublicKey, Message, signature, base, lambda_bits))

initial seed:  0
The global derangement for multidimensional entropic multiplications is:  [3, 1, 4, 2]

p =  10055855947456947824680518748654384595609524365444295033292671082791323022555160232601405723625177570767523893639864538140315412108959927459825236754597199
log_2(p) =  512

q =  5027927973728473912340259374327192297804762182722147516646335541395661511277580116300702861812588785383761946819932269070157706054479963729912618377298809
log_2(q) =  511

Information about the finite field:  Finite Field of size 10055855947456947824680518748654384595609524365444295033292671082791323022555160232601405723625177570767523893639864538140315412108959927459825236754597199

aa1 =  5083521238499181616107103435540117463555863868499725717345286618378307579761303457915289965842449989320867780251139340372938505409275428692727806563961170
aa3 =  2432424042971493215259752716409360521732123369897594983538095158510825326037876699129932315236342603157409792578609891994907734721051329531278165610547467
a

signature =  ([(8206651627273645745198768486409488139370461550670311960499234045181569853549812902058236333647611243823723264300922027504841065564136225345427915383848146, 8952314330825627829268630841979377750471693219796782895102913802499453109646066317253032483792120882365204388031225239305799976481475597033904914959105178), (6289190683276078551633044548644684607912880163877323580249318738921557404985081996647289081406953591393848100021905208687109229536450837925998262657066537, 4320373113216447575037745468038940291648626834697375637466470602974315881276244094969803950067454755667230335977711242184692743125160470672095035019414437), (9652785361496609040736616374726356152523931756508973550534796024819943137307610114484241410667695054370264808792771288080693042156105696352827045581182525, 4918499578557339391925144197571191722002493463498482325693376024306135531908682479145604627135901698337448166175534667074097840847752395978861304001531712), (487999155665799794464930615481286618385353